# COMP6481/8481 - class 9 - topic modelling 


In [1]:
# ! pip install pyLDAvis

In [2]:
import nltk
import pyLDAvis
import pyLDAvis.gensim
import gensim 



/Users/ayeshababar/opt/anaconda3/lib/python3.9/site-packages/scipy/sparse/sparsetools.py:21: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  _deprecated()


In [3]:
# only run this cell if you've never downloaded nltk files before on this jupyter setup
# to run this cell, delete the # sign at the start of the next line
#nltk.download()


# in the dialogue, choose to download 'book' (if you get a GUI) 
# or select download and type `book` (if you get a text interface)
#
# Download may take a while.
# quit the downloader dialogue afterwards

## Movie reviews

We'll be working with some data containing reviews of movies

Let's understand the data we have.

If you want, you can also run:
* help(movie_reviews)
* movie_reviews.fileids (to see the different ids)

(see https://www.nltk.org/api/nltk.corpus.util.html#nltk.corpus.util.LazyCorpusLoader)



In [4]:
from nltk.corpus import movie_reviews
print(len(movie_reviews.raw()))
# to look at all data, we'll need to restrict how much we view (as data are too big)
print(movie_reviews.raw()[0:1000])


7786004
plot : two teen couples go to a church party , drink and then drive . 
they get into an accident . 
one of the guys dies , but his girlfriend continues to see him in her life , and has nightmares . 
what's the deal ? 
watch the movie and " sorta " find out . . . 
critique : a mind-fuck movie for the teen generation that touches on a very cool idea , but presents it in a very bad package . 
which is what makes this review an even harder one to write , since i generally applaud films which attempt to break the mold , mess with your head and such ( lost highway & memento ) , but there are good and bad ways of making all types of films , and these folks just didn't snag this one correctly . 
they seem to have taken this pretty neat concept , but executed it terribly . 
so what are the problems with the movie ? 
well , its main problem is that it's simply too jumbled . 
it starts off " normal " but then downshifts into this " fantasy " world in which you , as an audience member , ha

In [5]:
movie_reviews.fileids()

['neg/cv000_29416.txt',
 'neg/cv001_19502.txt',
 'neg/cv002_17424.txt',
 'neg/cv003_12683.txt',
 'neg/cv004_12641.txt',
 'neg/cv005_29357.txt',
 'neg/cv006_17022.txt',
 'neg/cv007_4992.txt',
 'neg/cv008_29326.txt',
 'neg/cv009_29417.txt',
 'neg/cv010_29063.txt',
 'neg/cv011_13044.txt',
 'neg/cv012_29411.txt',
 'neg/cv013_10494.txt',
 'neg/cv014_15600.txt',
 'neg/cv015_29356.txt',
 'neg/cv016_4348.txt',
 'neg/cv017_23487.txt',
 'neg/cv018_21672.txt',
 'neg/cv019_16117.txt',
 'neg/cv020_9234.txt',
 'neg/cv021_17313.txt',
 'neg/cv022_14227.txt',
 'neg/cv023_13847.txt',
 'neg/cv024_7033.txt',
 'neg/cv025_29825.txt',
 'neg/cv026_29229.txt',
 'neg/cv027_26270.txt',
 'neg/cv028_26964.txt',
 'neg/cv029_19943.txt',
 'neg/cv030_22893.txt',
 'neg/cv031_19540.txt',
 'neg/cv032_23718.txt',
 'neg/cv033_25680.txt',
 'neg/cv034_29446.txt',
 'neg/cv035_3343.txt',
 'neg/cv036_18385.txt',
 'neg/cv037_19798.txt',
 'neg/cv038_9781.txt',
 'neg/cv039_5963.txt',
 'neg/cv040_8829.txt',
 'neg/cv041_22364.txt',


In [6]:
# We'll want to do some preprocessing. 
# Run this (slightly adapted) code from the topic modelling notebook on moodle

def preprocess_mr(text, stops):
    # here, text is already tokenised and lower-cased

    # perform stemming, remove provided stopwords
    porter = nltk.stem.PorterStemmer()
    new_t = []
    for t in text:
        if t not in stops:
            new_t.append(porter.stem(t))

    # No need to pos_tag all tokens, 
    # as this isn't helpful for topic modelling techniques we'll look at today
    # so let's return the text we've preprocessed
    return new_t


# let's also generate stopwords data to use as part of our function
# stopwords can be removed from our data, they are common words which are not likely to 
# hold much meaningful content for our needs (e.g. 'they', 'the', 'and', etc)
from nltk.corpus import stopwords
stopwords = set(stopwords.words("english"))
# let's add some basic punctuation to our set of stopwords, for these to be ignored as well
punct = set([",", ".", "'", ":", "[", "]"])
stopwords = stopwords.union(punct)


print("finished running, ready for next step")



finished running, ready for next step


In [7]:
# Run this cell to extract movie reviews and put them into a list called mr 
# (this may take a minute)
#

mr = []

for fileid in movie_reviews.fileids():
    # let's pull our reviews into this notebook using the words() function
    # we use the words() function with the id of the file to retrieve a single review
    words = movie_reviews.words(fileid)
    tokens = preprocess_mr(words, stopwords)
    mr.append(tokens) 


# we should have 2000 entries?
print(len(mr))


2000


In [8]:
# mr is now our list of texts. Let's look at a few
for i in range (8, 12):
    print(mr[i])

['call', 'road', 'trip', 'walk', 'wound', 'stellan', 'skarsg', '?', 'rd', 'play', 'convincingli', 'zombifi', 'drunken', 'loser', 'difficult', 'spend', 'nearli', 'two', 'hour', 'screen', 'time', 'smelli', 'booz', '-', 'presenc', 'yet', 'ever', '-', 'reliabl', 'swedish', 'actor', 'add', 'depth', 'signific', 'otherwis', 'plod', 'forgett', 'aberdeen', 'sentiment', 'pain', 'mundan', 'european', 'drama', 'playwright', 'august', 'strindberg', 'built', 'career', 'famili', 'relationship', 'paralyz', 'secret', 'unabl', 'express', 'long', 'hour', 'far', 'late', 'accur', 'reflect', 'aberdeen', 'strive', 'focus', 'pair', 'alcohol', 'father', 'toma', '(', 'skarsg', '?', 'rd', ')', 'alien', 'openli', 'hostil', 'yuppi', 'daughter', 'kaisa', '(', 'lena', 'headey', 'gossip', ')', 'spoken', 'year', 'even', 'make', 'long', 'trip', 'norway', 'aberdeen', 'scotland', 'automobil', 'kaisa', 'mother', '(', 'charlott', 'rampl', 'sand', ')', 'rot', 'away', 'hospit', 'bed', 'cancer', 'soap', 'opera', 'twist', 'mot

### 1. Using the jupyter notebook on topic modelling in moodle as a guide (also included in this class folder on raptor), generate a corpus and a Dictionary for doing LDA topic modelling from the data in mr

In [9]:
from gensim.corpora.dictionary import Dictionary

# Create a corpus from a list of texts
mr_dictionary = Dictionary(mr)
mr_corpus = [mr_dictionary.doc2bow(text) for text in mr]

In [10]:
mr_dictionary.token2id

{'!': 0,
 '"': 1,
 '&': 2,
 '(': 3,
 ')': 4,
 '-': 5,
 '/': 6,
 '10': 7,
 '2': 8,
 '20': 9,
 '3': 10,
 '4': 11,
 '7': 12,
 '8': 13,
 '9': 14,
 '?': 15,
 'accid': 16,
 'actor': 17,
 'actual': 18,
 'ago': 19,
 'also': 20,
 'although': 21,
 'alway': 22,
 'american': 23,
 'appar': 24,
 'apparit': 25,
 'applaud': 26,
 'arrow': 27,
 'assum': 28,
 'attempt': 29,
 'audienc': 30,
 'away': 31,
 'back': 32,
 'bad': 33,
 'beauti': 34,
 'bentley': 35,
 'big': 36,
 'biggest': 37,
 'bit': 38,
 'blair': 39,
 'bottom': 40,
 'break': 41,
 'came': 42,
 'charact': 43,
 'chase': 44,
 'chop': 45,
 'church': 46,
 'clue': 47,
 'come': 48,
 'complet': 49,
 'concept': 50,
 'confus': 51,
 'continu': 52,
 'cool': 53,
 'correctli': 54,
 'coupl': 55,
 'crazi': 56,
 'critiqu': 57,
 'crow': 58,
 'dead': 59,
 'deal': 60,
 'decent': 61,
 'decid': 62,
 'despit': 63,
 'die': 64,
 'differ': 65,
 'dig': 66,
 'director': 67,
 'disappear': 68,
 'downshift': 69,
 'dream': 70,
 'drink': 71,
 'drive': 72,
 'echo': 73,
 'edg': 7

In [11]:
mr_corpus

[[(0, 3),
  (1, 10),
  (2, 1),
  (3, 9),
  (4, 9),
  (5, 10),
  (6, 8),
  (7, 10),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 2),
  (13, 1),
  (14, 2),
  (15, 6),
  (16, 1),
  (17, 1),
  (18, 2),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 2),
  (25, 1),
  (26, 1),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 2),
  (31, 2),
  (32, 1),
  (33, 2),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 2),
  (38, 1),
  (39, 1),
  (40, 1),
  (41, 1),
  (42, 1),
  (43, 3),
  (44, 2),
  (45, 1),
  (46, 1),
  (47, 1),
  (48, 2),
  (49, 1),
  (50, 1),
  (51, 1),
  (52, 1),
  (53, 2),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 1),
  (58, 2),
  (59, 2),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 1),
  (64, 1),
  (65, 1),
  (66, 1),
  (67, 1),
  (68, 1),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 1),
  (79, 3),
  (80, 1),
  (81, 3),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 1),
  (90, 1),
  (91,

### 2. Build an LDA topic model that can detect 5 topics in the data, taking 5 passes through the iterative process. 
Print the resulting 5 topics that get identified.
Again you can use the jupyter notebook code as a guide

In [12]:
from gensim import models

lda = models.ldamodel.LdaModel(mr_corpus, num_topics=5, id2word=mr_dictionary, passes=5)

topics = lda.show_topics(formatted=False)
for t in topics:
    #print(t)
    print(t[0], [x[0] for x in t[1]])

0 ['-', '"', 'film', ')', '(', 'one', 'like', 'charact', '?', 'movi']
1 ['-', ')', 'movi', '(', 'film', '"', 'one', '=', 'like', 'charact']
2 ['-', 'film', ')', '(', 'movi', 'one', '"', '?', 'get', 'charact']
3 ['"', '-', '(', ')', 'film', 'movi', 'one', 'charact', '?', 'like']
4 ['"', '-', '(', ')', 'film', 'movi', 'one', 'like', 'charact', 'make']


### 3. Inspect your results. Can you identify an abstract topic for each list of words?

The topics identified are not very clear which implies that the data does not have a lot of well-seperated topics. Additionally the data requires further pre-processing to get rid of characters in the list of topics.


### 4. Take steps to improve your results. Firstly, rebuild the LDA topic model taking 10 passes through iterative process.
Print the resulting 5 topics that get identified.

In [13]:
lda = models.ldamodel.LdaModel(mr_corpus, num_topics=5, id2word=mr_dictionary, passes=10)

topics = lda.show_topics(formatted=False)
for t in topics:
    #print(t)
    print(t[0], [x[0] for x in t[1]])

0 ['"', '-', ')', '(', 'film', 'movi', 'one', 'like', 'charact', 'get']
1 ['-', ')', '(', 'film', '"', 'one', '?', 'movi', 'charact', 'like']
2 ['film', 'movi', '(', ')', '-', '"', 'one', '!', 'time', 'like']
3 ['"', '-', ')', '(', 'film', 'movi', 'one', 'charact', 'like', '?']
4 ['"', '-', '(', ')', 'film', 'movi', 'one', 'like', 'charact', 'make']


### 5. Now, try rebuilding the LDA topic model to take 10 passes through the iterative process, but looking for 10 topics instead of 5.  

Print the resulting 10 topics that get identified.

NB as LDA is probabilistic, the topics may not be represented by the same words each time as LDA is non-deterministic

In [14]:
lda = models.ldamodel.LdaModel(mr_corpus, num_topics=10, id2word=mr_dictionary, passes=10)

topics = lda.show_topics(formatted=False)
for t in topics:
    #print(t)
    print(t[0], [x[0] for x in t[1]])

0 ['movi', '-', ')', '(', 'film', 'one', '"', 'like', '?', 'get']
1 ['film', '-', ')', '(', '"', 'one', 'charact', 'like', 'make', 'stori']
2 ['"', '-', ')', '(', 'film', 'movi', 'one', 'like', '?', 'charact']
3 ['-', ')', '(', 'truman', 'film', 'ape', '"', 'one', 'movi', 'play']
4 ['-', '(', ')', '"', 'film', 'one', 'movi', 'charact', 'time', 'like']
5 ['chucki', 'lumumba', '*', 'doll', 'peck', ')', 'nixon', 'ebouaney', '(', 'bride']
6 ['film', '-', ')', '(', '"', 'movi', '?', 'one', 'charact', 'like']
7 ['"', 'film', '-', ')', '(', 'one', 'movi', 'like', '?', 'make']
8 ['"', ')', '(', '-', 'film', 'one', 'movi', 'like', 'make', 'get']
9 ['-', 'flynt', ')', '(', 'life', 'film', '"', 'make', 'one', 'guido']


### 6. From 3, 4 and 5, which list of topics do you think is most useful in identifying distinct topics in the data? Why?

*you can write your answer here if it is helpful to record it*


### 7. Choose a number of topics and a number of passes through the iterative process that you think worked well from your work above (or from trying other choices)
Now try removing frequent tokens from the topics, re-preprocessing the data, and seeing if you can improve the topic modelling results further. Feel free to experiment!

How much can you improve the quality of the lists of words that you've identified as topics?

*Hint: stopwords variables contains the current list of stopwords and other tokens that are removed from the data during preprocessing. You can add tokens to this list, and then call the preprocess_mr() function with the new stopwords as the second parameter. See the topic modelling jupyter notebook from moodle as a guide, again.*


In [15]:
mr_dictionary.values()

ValuesView(<gensim.corpora.dictionary.Dictionary object at 0x7fceb1cebc10>)

In [16]:
remove_words = ['"', '-', '--', '?', '(', ')', '=', "like", "make", "one"]
stopwords = stopwords.union(remove_words)

In [17]:
mr = []

for fileid in movie_reviews.fileids():
    # let's pull our reviews into this notebook using the words() function
    # we use the words() function with the id of the file to retrieve a single review
    words = movie_reviews.words(fileid)
    tokens = preprocess_mr(words, stopwords)
    mr.append(tokens) 


# we should have 2000 entries?
print(len(mr))


2000


In [18]:
# Create a corpus from a list of texts
mr_dictionary = Dictionary(mr)
mr_corpus = [mr_dictionary.doc2bow(text) for text in mr]

In [23]:

lda = models.ldamodel.LdaModel(mr_corpus, num_topics=5, id2word=mr_dictionary, passes=10)

topics = lda.show_topics(formatted=False)
for t in topics:
    #print(t)
    print(t[0], [x[0] for x in t[1]])

0 ['film', 'movi', 'charact', 'get', 'even', 'time', 'play', 'scene', 'good', 'see']
1 ['film', 'movi', 'charact', 'get', 'time', 'scene', 'play', 'good', 'two', 'stori']
2 ['movi', 'film', 'get', '!', 'even', '*', 'time', 'bad', 'good', 'scene']
3 ['film', 'charact', 'movi', 'time', 'stori', 'play', 'scene', 'get', 'see', 'way']
4 ['film', 'movi', 'charact', 'time', 'stori', 'scene', 'get', 'well', 'good', 'alien']


In [24]:
# Creating Topic Visualizations 
pyLDAvis.enable_notebook()
p = pyLDAvis.gensim.prepare(lda, mr_corpus, mr_dictionary)
p

/Users/ayeshababar/opt/anaconda3/lib/python3.9/site-packages/pyLDAvis/_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.006964  0.009968       1        1  26.558373
1     -0.006131  0.028558       2        1  22.799792
3     -0.047595 -0.008456       3        1  17.606349
2      0.042272  0.016594       4        1  17.111916
4      0.018418 -0.046664       5        1  15.923569, topic_info=       Term          Freq         Total Category  logprob  loglift
142    movi   6747.000000   6747.000000  Default  30.0000  30.0000
830   alien    610.000000    610.000000  Default  29.0000  29.0000
1951      *   1022.000000   1022.000000  Default  28.0000  28.0000
0         !   1657.000000   1657.000000  Default  27.0000  27.0000
88     film  10815.000000  10815.000000  Default  26.0000  26.0000
...     ...           ...           ...      ...      ...      ...
273    much    301.213164   1981.805153   Topic5  -5.9200  -0.0466
124    life    276.388426   1531.923640   Topic5  -6.0060   0.1249
215     two    288.033247   1847.748986   Topic5  -5.9648  -0.0213
127    look    282.069864   1833.659388   Topic5  -5.9857  -0.0345
163    play    278.457065   2303.052993   Topic5  -5.9986  -0.2754

[474 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
0         1  0.307637     !
0         2  0.111594     !
0         3  0.078417     !
0         4  0.340210     !
0         5  0.162263     !
...     ...       ...   ...
234       1  0.308378  year
234       2  0.203195  year
234       3  0.167934  year
234       4  0.138650  year
234       5  0.182278  year

[1022 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 4, 3, 5])

As pointed out earlier the data does not seem to have well-seperated topics. The most common words appearing in almost all topics are 'film', 'movie' and 'charater' which is expected since this is a movie review dataset.